In [1]:
%%capture
!pip install -q transformers einops accelerate langchain bitsandbytes

In [2]:
!huggingface-cli login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    To login, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Enter your token (input will not be visible): 
Add token as git credential? (Y/n) y
Token is valid (permission: fineGrained).
Cannot authenticate through git-credential as no helper is defined on your machine.
You might have to re-authenticate when pushing to the Hugging Face Hub.
Run the following command in your termin

In [3]:
!mkdir pdfs

In [4]:
%%capture
pip install pypdf

In [5]:
%%capture
pip install langchain-community

In [6]:
from langchain.document_loaders import PyPDFDirectoryLoader

In [7]:
loader=PyPDFDirectoryLoader("pdfs")

In [8]:
data=loader.load()

In [9]:
# we are going to create the chunks
from langchain.text_splitter import RecursiveCharacterTextSplitter

In [10]:
text_chunks=RecursiveCharacterTextSplitter(chunk_size=300,chunk_overlap=20)

In [11]:
chunks=text_chunks.split_documents(data)

In [13]:
len(chunks)

235

In [14]:
# creating embeddings using huggingface embedding model
from langchain.embeddings import HuggingFaceEmbeddings

In [15]:
%%capture
pip install sentence-transformers

In [16]:
embeddings=HuggingFaceEmbeddings(model_name="sentence-transformers/all-MiniLM-L6-v2")

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:139: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 0.3.0. An updated version of the class exists in the langchain-huggingface package and should be used instead. To use it run `pip install -U langchain-huggingface` and import as `from langchain_huggingface import HuggingFaceEmbeddings`.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/sentence_transformers/cross_encoder/CrossEncoder.py:11: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/sett

modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.7k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/350 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [17]:
%%capture
pip install faiss-cpu

In [18]:
from langchain.vectorstores import FAISS

In [19]:
vectordabase=FAISS.from_documents(chunks,embeddings)

In [21]:
question="what is generative ai?"

In [22]:
vectordabase.similarity_search(question)

[Document(metadata={'source': 'pdfs/Generative AI.pdf', 'page': 1}, page_content='Generative AI \nGenerative AI refers to a branch of artificial intelligence that focuses on creating \nmodels and algorithms capable of generating new, original content, such as \nimages, text, music, and even videos. Unlike traditional AI models that are trained'),
 Document(metadata={'source': 'pdfs/Generative AI.pdf', 'page': 78}, page_content='Generative AI \nGenerative AI is a type of AI that can create new content including text, code, images and music. Generative AI models are trained \non large datasets of existing content, learning to identify patterns in data and using those patterns to generate new content.'),
 Document(metadata={'source': 'pdfs/Generative AI.pdf', 'page': 75}, page_content='music or even generating code. Instead of relying on pre-programmed responses, \ngenerative AI leverages its understanding of language to produce truly original \noutputs, making it a powerful tool for crea

In [23]:
model="google/flan-t5-large"

In [24]:
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM,pipeline
from langchain import HuggingFacePipeline

In [25]:
tokenizer=AutoTokenizer.from_pretrained(model) # tokenization(token)
model1=AutoModelForSeq2SeqLM.from_pretrained(model) # (generation)

tokenizer_config.json:   0%|          | 0.00/2.54k [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.42M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/2.20k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/662 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/3.13G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/147 [00:00<?, ?B/s]

In [26]:
pipe=pipeline("text2text-generation",model=model1,tokenizer=tokenizer)

In [27]:
llm=HuggingFacePipeline(pipeline=pipe, model_kwargs={"temperature": 0, "max_length": 512})

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:139: LangChainDeprecationWarning: The class `HuggingFacePipeline` was deprecated in LangChain 0.0.37 and will be removed in 0.3. An updated version of the class exists in the langchain-huggingface package and should be used instead. To use it run `pip install -U langchain-huggingface` and import as `from langchain_huggingface import HuggingFacePipeline`.
  warn_deprecated(


In [28]:
# retrieval qa takes prompt template and llm
from langchain.prompts import PromptTemplate

template = """use the context to provide a concise answer and if you don't know just say don't now.
{context}
Question: {question}
Helpful Answer:"""
QA_CHAIN_PROMPT = PromptTemplate.from_template(template)

In [29]:
from langchain.chains import RetrievalQA
qa_chain = RetrievalQA.from_chain_type(
    llm, retriever=vectordabase.as_retriever(), chain_type_kwargs={"prompt": QA_CHAIN_PROMPT}
)

In [31]:
qa_chain.run("what is generative ai?")

/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1249: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(


'a branch of artificial intelligence that focuses on creating models and algorithms capable of generating new'

In [32]:
question="more detail about generative ai?"
result = qa_chain({"query": question})
print(result["result"])

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:139: LangChainDeprecationWarning: The method `Chain.__call__` was deprecated in langchain 0.1.0 and will be removed in 0.3.0. Use invoke instead.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1249: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(


Generative AI models are trained on large datasets of existing content, learning to identify patterns


In [33]:
def fetch(question,history):
  result=qa_chain({"query":question})
  return result["result"]

In [34]:
%%capture
pip install gradio

In [35]:
import gradio as gr

In [36]:
gr.ChatInterface(
    fetch,
    chatbot=gr.Chatbot(height=300),
    textbox=gr.Textbox(placeholder="You can ask a question", container=False, scale=7),
    title="A Generative AI chatbot",
    description="You can ask questions related to Generative AI",
    theme="soft",
    examples=["what is Generative AI?", "what are the examples?", "what is LLM?"],
    cache_examples=True,
    retry_btn=None,
    undo_btn="Delete Previous",
    clear_btn="Clear",
).launch(share=True)

Caching examples at: '/content/gradio_cached_examples/15'
Caching example 1/3


/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1249: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(


Caching example 2/3


/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1249: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(


Caching example 3/3


/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1249: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(


Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
Running on public URL: https://2e069e3f5ca0f0f8da.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)
